In [9]:
import os
import torch
import json
from datasets import load_dataset
from transformers import (
    AutoModelForCausalLM,
    AutoTokenizer,
    BitsAndBytesConfig,
    HfArgumentParser,
    TrainingArguments,
    pipeline,
    logging,
    GenerationConfig
)
import pickle
import json
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import PorterStemmer
nltk.download('stopwords')
nltk.download('punkt')


from gpt_ner_api_codes.prompts_all import *

#from peft import LoraConfig, PeftModel, get_peft_model
#from trl import SFTTrainer

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\z004r5cc\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\z004r5cc\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


# data processing for instruction fine-tuning - text, input, and instruction

In [2]:
dataset_name = "yahma/alpaca-cleaned"
dataset = load_dataset(dataset_name, split="train")
#raw_datasets_train = dataset.train_test_split( train_size=0.999999 )["train"]
raw_datasets_train = dataset.train_test_split( train_size=0.0006 )["train"]

combined_columns = []
print(len(raw_datasets_train["instruction"]))
for i in range(len(raw_datasets_train["instruction"])):
  row = raw_datasets_train["instruction"][i] + raw_datasets_train["input"][i] + raw_datasets_train["output"][i]
  combined_columns.append(row)

dataset = raw_datasets_train.add_column("text", combined_columns)

31


Flattening the indices:   0%|          | 0/31 [00:00<?, ? examples/s]

In [7]:
#dataset, dataset['output'][0],dataset['input'][0],dataset['instruction'][0],dataset['text'][0]

# data processing for instruction fine-tuning - from pickle binary list to jsonl

In [8]:
def process_to_llama2_finetuning_format(path_in_sentence, path_in_entities, path_out):
    with open(path_in_sentence, 'br') as data:
        f = pickle.load(data)
    #load the sentence
    #with open(path_in_sentence, 'r', encoding='utf-8') as f:
        sentence_list = []
        for line in f:
            sentence_list.append(line)     
    #print(sentence_list)
    
    
    with open(path_in_entities, "br") as data:   #Pickling
        f = pickle.load(data)
    #load the entities
    #with open(path_in_entities, 'r', encoding='utf-8') as f:   
        entity_list = []
        entity_for_one_sentence = ""
        for i,line in enumerate(f):
#             entity_for_one_sentence = entity_for_one_sentence + line
#             print(i, line)
#             if line == "\n":
#                 print(entity_for_one_sentence)
#                 entity_list.append( entity_for_one_sentence )
#                 entity_for_one_sentence = ""
            entity_list.append( line )

    
    #sentence_list = sentence_list.decode()
    #entity_list = entity_list.decode()
    # write everything in a new document
    #print(sentence_list[0].type)
    #print(entity_list, sentence_list[0])
    print(len(entity_list), len(sentence_list))
    instruction = "Extract the entities in the input sentence below:\n"
    with open(path_out, 'w', encoding='utf-8') as e:  
        new_format = {}
        for i in range(len(entity_list)):
            #print(str(sentence_list[i]), str(entity_list[i]))
            new_format["instruction"] = instruction
            new_format["input"] =  str(sentence_list[i])
            new_format["output"] =  str(entity_list[i])

            e.write(json.dumps(new_format) + "\n")   
            new_format = {}
            

# prepare dataset for instruction fine-tuning

In [ ]:
path_in_sentence = "./data/immutable_data_formal/sen_thf_train.txt"
path_in_entities = "./data/immutable_data_formal/dem_thf_train.txt"
path_out = "./data/immutable_data_formal/llama2chat7b_thf_train.jsonl"
process_to_llama2_finetuning_format(path_in_sentence, path_in_entities, path_out)

In [76]:
path_in_sentence = "./data/immutable_data_formal/sen_assembly_train.txt"
path_in_entities = "./data/immutable_data_formal/dem_assembly_train.txt"
path_out = "./data/immutable_data_formal/llama2chat7b_assembly_train.jsonl"
process_to_llama2_finetuning_format(path_in_sentence, path_in_entities, path_out)

776 776


In [ ]:
path_in_sentence = "./data/immutable_data_formal/sen_fabner_train.txt"
path_in_entities = "./data/immutable_data_formal/dem_fabner_train.txt"
path_out = "./data/immutable_data_formal/llama2chat7b_fabner_train.jsonl"
process_to_llama2_finetuning_format(path_in_sentence, path_in_entities, path_out)

 # prepare dataset for fine-tuning

# data processing for instruction fine-tuning - from jsonl list to jsonl

In [69]:
def change_output_format_to_tokens_tags(path_in_sentence = "unknown", path_in_entities = "unknown", sentence_list = [], entity_list = [], path_out = "unknown"):
    
    #################################
    # load the pickle list of data, both for original sentences and entities
    #################################
    if path_in_sentence != "unknown":
        with open(path_in_sentence, 'br') as data:
            f = pickle.load(data)
        # with open(path_in_sentence, 'r', encoding='utf-8') as f:
            sentence_list = []
            for line in f:
                sentence_list.append(line)   

        with open(path_in_entities, "br") as data:   #Pickling
            f = pickle.load(data)    
            path_in_entities = f
            print("length of f: ", len(f))

        ## assign the loaded list to new variable for the code below        
        sentences_input = sentence_list
        response = path_in_entities
        print(len(sentences_input), len(response))
        
    elif path_in_sentence == "unknown":           
        ## assign the loaded list to new variable for the code below        
        sentences_input = sentence_list
        response = entity_list
        print(len(sentences_input), len(response))
    
    #################################
    # process the original sentence and gpt output format into tokens and ner_tags
    #################################
    total_list = []
    #print(response[-1] + "\n")
    for i, sin_response in enumerate(response):
        #print( i, response[i], sentences_input[i] )
        dict_one_sentence = {}
        dict_one_sentence["tokens"] = sentences_input[i].split(" ")
        dict_one_sentence["ner_tags"] = ["O" for k in range(len(dict_one_sentence["tokens"])+1)]
        ## print(dict_one_sentence)
        sin_item_entity_list = sin_response.split("\n\n")[0] # just to prevent \n split the \n\n
        sin_item_entity_list = sin_item_entity_list.split("\n")
        
        for sin_item_entity in sin_item_entity_list:
            #print(sin_item_entity)
            if len( sin_item_entity.split(": ") ) == 1:
                # ignore the case the "no entity in this sentence" "O" is assigned before.
                continue
            else:
                # prevent Nd : YAG: MATE
                sin_entity = sin_item_entity.split(": ")[-1]
                sin_item = sin_item_entity.split(": " + sin_entity)[0]
            #print(sin_item, sin_entity)

            if sin_item == "": # dolly output empty entities
                sin_item = "Scheisse"
            len_sin_item = len(sin_item.split())
                
            except_item = sentences_input[i].split(sin_item) 
            if len(except_item) == 1:
                # in case that sim_item is the first word of the sentence, set position_begin_item = 0
                position_begin_item = 0
                # update the ner_tags for len(except_item) == 1 and 2      
                for k in range(len_sin_item):
                    if position_begin_item+k >= len(dict_one_sentence["ner_tags"]):
                    # this if condition is used to make sure that we can at least get the results from evaluation
                    # Sometimes sin_items can not be separated correctly    
                        break
                    dict_one_sentence["ner_tags"][position_begin_item+k] = sin_entity


            elif len(except_item) == 2: 
                # pick the index of this sin_item as position_begin_item
                position_begin_item = len (   word_tokenize(  except_item[0].strip() )    )      
                # update the ner_tags for len(except_item) == 1 and 2    
                for k in range(len_sin_item):
                    dict_one_sentence["ner_tags"][position_begin_item+k] = sin_entity     
                         
            else:
                # in case that sim_items happen twice in the original sentence, len(except_item) > 2
                for sin_item_index in range(len(except_item)-1):
                    position_begin_item = len (   word_tokenize(  except_item[sin_item_index].strip() )    )   
                    for k in range(len_sin_item):
                        if dict_one_sentence["ner_tags"][position_begin_item+k] != "O":
                            dict_one_sentence["ner_tags"][position_begin_item+k] = sin_entity
                #continue 

            # update the ner_tags for len(except_item) == 1 and 2      
            #for k in range(len_sin_item):
            #    dict_one_sentence["ner_tags"][position_begin_item+k] = sin_entity

        total_list.append(dict_one_sentence)
        
    #dumps the list of dictionary    
    with open(path_out, 'w', encoding='utf-8') as e:  
        for dictionary in total_list:
            e.write(json.dumps(dictionary) + "\n")   
            
    return total_list

In [70]:
##############################################################################################
#### load data from the training dataset and split the validation dataset there

def split_dev_dataset_input_pickle(path_original_sentence, path_entities, path_tokens_tags, num_input=2, demon_size=20, stratify = True):
    
    path_original_sentence = os.path.abspath(path_original_sentence)
    path_entities = os.path.abspath(path_entities)
    path_tokens_tags = os.path.abspath(path_tokens_tags)
    
    #with open (path_original_sentence, encoding='utf-8') as f:
        #sentences = f.readlines()
        #sentences = sentences[:-1]
    with open(path_original_sentence, 'br') as data:
        f = pickle.load(data)
        sentences = f

    #with open (path_entities, encoding='utf-8') as f:
        #demonstrations = f.read()
        #demonstrations = demonstrations[:-1]
        #demonstrations = demonstrations.split("\n\n")
    with open(path_in_entities, "br") as data:   #Pickling
        f = pickle.load(data)     
        demonstrations = f
        for i in range(len(demonstrations)):
            demonstrations[i] = demonstrations[i] + "\n\n"
    with open (path_tokens_tags, encoding='utf-8') as f: 
        token_tags = []
        for line in f:
            token_tag = json.loads(line)
            token_tags.append(token_tag)
        token_tags = token_tags[:-1]
    ## get sentences, demonstrations and token_tags    

    if stratify:
        # get entities of each sentence in the few-shot dataset
        entity_list =  get_entity_from_demonstrations(demonstrations) 
        #print(len(sentences), len(demonstrations), len(entity_list) )
        sentences_dev, sentences_input, sentences_train, demonstrations_dev, demonstrations_input_solutions, demonstrations_train = stratify_the_dataset(sentences, demonstrations, entity_list, demon_size, num_input)
    else:
        sentences_train, sentences_val, demonstrations_train, demonstrations_val = train_test_split(sentences, demonstrations, test_size=num_input, random_state=42)
        
    return sentences_train, sentences_val, demonstrations_train, demonstrations_val 





# thin-film technology dataset

In [71]:
with open("./data/immutable_data_formal/sen_thf_train.txt", 'br') as data:
        f = pickle.load(data)
        print(len(f))

3760


In [79]:
# split validation dataset from training dataset
path_in_sentence = "./data/immutable_data_formal/sen_thf_train.txt"
path_in_entities = "./data/immutable_data_formal/dem_thf_train.txt"
path_tokens_tags = "./data/thin-film-technology-dataset/thin_film_head_technology_total.jsonl"
sentences_train, sentences_val, demonstrations_train, demonstrations_val = split_dev_dataset_input_pickle(path_in_sentence, path_in_entities, path_tokens_tags, num_input = 300, demon_size = 10, stratify = False)
print(len(sentences_train), len(sentences_val))
print(len(demonstrations_train), len(demonstrations_val))

3460 300
3460 300


In [80]:
path_out = "./salmon/data_finetuning/finetune_bert_based_entity_model_thf/formal_thf_train.jsonl"
change_output_format_to_tokens_tags(entity_list = demonstrations_train, sentence_list = sentences_train, path_out = path_out)

3460 3460


[{'tokens': ['The',
   'coil',
   'passes',
   'through',
   'a',
   'magnetic',
   'yoke',
   'having',
   'an',
   'open',
   'end',
   'and',
   'a',
   'closed',
   'end',
   'and',
   'is',
   'electrically',
   'insulated',
   'from',
   'the',
   'yoke',
   '.',
   '\n'],
  'ner_tags': ['O',
   'Component',
   'O',
   'O',
   'O',
   'Component',
   'Component',
   'O',
   'O',
   'Location',
   'Location',
   'O',
   'O',
   'Location',
   'Component',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O']},
 {'tokens': ['The',
   'flow',
   'of',
   'the',
   'current',
   'at',
   'the',
   '45',
   'degree',
   'angle',
   'with',
   'respect',
   'to',
   'the',
   'free',
   'layer',
   'magnetization',
   'causes',
   'the',
   'AMR',
   'effect',
   'which',
   'is',
   'present',
   'in',
   'the',
   'free',
   'MR',
   'layer',
   'to',
   'be',
   'added',
   'to',
   'the',
   'spin',
   'valve',
   'sensor',
   'GMR',
   'effect',
   'and',

In [81]:
path_out = "./salmon/data_finetuning/finetune_bert_based_entity_model_thf/formal_thf_val.jsonl"
change_output_format_to_tokens_tags(entity_list = demonstrations_val, sentence_list = sentences_val, path_out = path_out)

300 300


[{'tokens': ['Further',
   ',',
   'a',
   'pair',
   'of',
   'electrodes',
   '(',
   '1',
   ',',
   '7',
   ')',
   'are',
   'formed',
   'so',
   'that',
   'the',
   'laminate',
   'comprising',
   'the',
   'above',
   'layers',
   'is',
   'sandwiched',
   'between',
   'the',
   'electrodes',
   '.',
   '\n'],
  'ner_tags': ['O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'Component',
   'O',
   'O',
   'Component',
   'Component',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O']},
 {'tokens': ['The',
   'present',
   'invention',
   'teaches',
   'a',
   'method',
   'for',
   'forming',
   'a',
   'balanced',
   'electrical',
   'half-bridge',
   'in',
   'parallel',
   'with',
   'the',
   'MR/GMR',
   'element',
   'of',
   'a',
   'read',
   'head',
   'so',
   'as',
   'to',
   'reduce',
   'readback',
   'noise',
   'caused',
   'by',
   'discharges',
   'between',
   'the',


In [82]:
# path_in_sentence = "./data/immutable_data_formal/sen_thf_train.txt"
# path_in_entities = "./data/immutable_data_formal/dem_thf_train.txt"
# # path out to salmon - the normal bert method 
# path_out = "./salmon/data_finetuning/finetune_bert_based_entity_model_thf/formal_thf_train.jsonl"
# change_output_format_to_tokens_tags(path_in_sentence, path_in_entities, path_out)

In [83]:
path_in_sentence = "./data/immutable_data_formal/sen_thf_input_30.txt"
path_in_entities = "./data/immutable_data_formal/dem_thf_input_30.txt"
# path out to salmon - the normal bert method 
path_out = "./salmon/data_finetuning/finetune_bert_based_entity_model_thf/formal_thf_test.jsonl"
change_output_format_to_tokens_tags(path_in_sentence, path_in_entities, path_out)

length of f:  500
500 500


[{'tokens': ['The',
   'pole',
   'pieces',
   'or',
   'core',
   'of',
   'the',
   'thin',
   'film',
   'head',
   'is',
   'electrically',
   'connected',
   'to',
   'the',
   'base',
   'substrate',
   'of',
   'the',
   'thin',
   'film',
   'head',
   '.',
   '\n'],
  'ner_tags': ['O',
   'Component',
   'Component',
   'O',
   'Component',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'Component',
   'Component',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O']},
 {'tokens': ['The',
   'pole',
   'portion',
   'and',
   'the',
   'insulating',
   'layer',
   'form',
   'a',
   'flat',
   'surface',
   'on',
   'a',
   'side',
   'of',
   'a',
   'recording',
   'gap',
   'layer',
   '.',
   '\n'],
  'ner_tags': ['O',
   'Location',
   'Location',
   'O',
   'O',
   'Component',
   'Component',
   'O',
   'O',
   'Component',
   'Component',
   'O',
   'O',
   'Attribution',
   'O',
   'O',
   'Component',
   'Component',
   

# assembly

In [23]:
# path_in_sentence = "./data/immutable_data_formal/sen_assembly_train.txt"
# path_in_entities = "./data/immutable_data_formal/dem_assembly_train.txt"
# path_out = "./salmon/data_finetuning/finetune_bert_based_entity_model_assembly/formal_assembly_train.jsonl"
# change_output_format_to_tokens_tags(path_in_sentence, path_in_entities, path_out)

length of f:  776
776 776


[{'tokens': ['#', 'Install', 'guide', '0', '\n'],
  'ner_tags': ['ID', 'OPER', 'O', 'O', 'O', 'O']},
 {'tokens': ['#',
   'even',
   'mm',
   'of',
   'now',
   'kit',
   'which',
   'Install',
   'When',
   'against',
   '0',
   '\n'],
  'ner_tags': ['ID',
   'O',
   'DIM',
   'O',
   'O',
   'O',
   'O',
   'OPER',
   'O',
   'RPOS',
   'O',
   'O',
   'O']},
 {'tokens': ['&',
   'Input',
   'item',
   '-LRB-',
   'regulator',
   'the',
   'so',
   '0',
   '\n'],
  'ner_tags': ['O', 'PART', 'O', 'O', 'PART', 'O', 'O', 'O', 'O', 'O']},
 {'tokens': ['&',
   'into',
   'exhaust',
   'rear',
   '769938',
   'on',
   'case',
   'Housing',
   'Torque',
   'show',
   '-RRB-',
   'for',
   'that',
   'only',
   '-RRB-',
   'accidentally',
   'Torque',
   'through',
   'Hardened',
   'Output',
   'With',
   'Housing',
   'the',
   'into',
   'AeroVee',
   'in',
   ',',
   'screw',
   'optional',
   'second',
   'try',
   "''",
   'of',
   'not',
   'AN3-3A',
   'Output',
   'connector',
   'a

In [85]:
# split validation dataset from training dataset
path_in_sentence = "./data/immutable_data_formal/sen_assembly_train.txt"
path_in_entities = "./data/immutable_data_formal/dem_assembly_train.txt"
path_tokens_tags = "./data/thin-film-technology-dataset/thin_film_head_technology_total.jsonl"
sentences_train, sentences_val, demonstrations_train, demonstrations_val = split_dev_dataset_input_pickle(path_in_sentence, path_in_entities, path_tokens_tags, num_input = 100, demon_size = 10, stratify = False)
print(len(sentences_train), len(sentences_val))
print(len(demonstrations_train), len(demonstrations_val))

676 100
676 100


In [86]:
path_out = "./salmon/data_finetuning/finetune_bert_based_entity_model_assembly/formal_assembly_train.jsonl"
change_output_format_to_tokens_tags(entity_list = demonstrations_train, sentence_list = sentences_train, path_out = path_out)

676 676


[{'tokens': ['-RRB-',
   'Item',
   'a',
   'The',
   'coat',
   'enough',
   '-RRB-',
   'it',
   'F',
   'the',
   'engine',
   'Check',
   'make',
   '11',
   '#',
   'bad',
   'you',
   'allow',
   'and',
   '0',
   '\n'],
  'ner_tags': ['O',
   'O',
   'O',
   'O',
   'PART',
   'O',
   'O',
   'O',
   'O',
   'O',
   'PART',
   'O',
   'O',
   'O',
   'ID',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O']},
 {'tokens': ['both',
   'Cover',
   'manual',
   'adding',
   'the',
   'is',
   'Heat',
   'Shaft',
   'bearing',
   'ft.-lbs',
   'vise',
   'field',
   '0',
   '\n'],
  'ner_tags': ['O',
   'PART',
   'O',
   'OPER',
   'O',
   'O',
   'OPER',
   'PART',
   'PART',
   'O',
   'O',
   'PART',
   'O',
   'O',
   'O']},
 {'tokens': ['as', 'Main', '11', 'the', '0', '\n'],
  'ner_tags': ['O', 'PART', 'O', 'O', 'O', 'O', 'O']},
 {'tokens': ['Pre-Load',
   'oil',
   '-RRB-',
   'against',
   'MUST',
   'see',
   'dedicated',
   ',',
   'the',
   'signal',
   'item',
   'of'

In [87]:
path_out = "./salmon/data_finetuning/finetune_bert_based_entity_model_assembly/formal_assembly_val.jsonl"
change_output_format_to_tokens_tags(entity_list = demonstrations_val, sentence_list = sentences_val, path_out = path_out)

100 100


[{'tokens': ['given',
   'housing',
   'attaching',
   'Note',
   'supplemental',
   '0',
   '\n'],
  'ner_tags': ['O', 'PART', 'O', 'O', 'O', 'O', 'O', 'O']},
 {'tokens': ['through',
   'Bearings',
   'the',
   'housing',
   'two',
   '-RRB-',
   'check',
   '-RRB-',
   'capacitor',
   'removed',
   'so',
   'number',
   'the',
   'down',
   'the',
   'the',
   'and',
   '-RRB-',
   'the',
   '0',
   '\n'],
  'ner_tags': ['RPOS',
   'PART',
   'O',
   'O',
   'O',
   'O',
   'OPER',
   'O',
   'PART',
   'OPER',
   'O',
   'O',
   'O',
   'RPOS',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O']},
 {'tokens': ['and',
   'to',
   'the',
   'of',
   'ends',
   '21',
   'Blade',
   'for',
   '-LRB-',
   'top',
   'the',
   'NOT',
   'shaft',
   'Bearing',
   'all',
   'kit',
   '-LRB-',
   'the',
   'front',
   'DO',
   'the',
   'a',
   'seat',
   'down',
   'propeller',
   'Above',
   'See',
   'item',
   '0',
   '\n'],
  'ner_tags': ['O',
   'O',
   'O',
   'O',
   'O',


In [88]:
path_in_sentence = "./data/immutable_data_formal/sen_assembly_input_30.txt"
path_in_entities = "./data/immutable_data_formal/dem_assembly_input_30.txt"
path_out = "./salmon/data_finetuning/finetune_bert_based_entity_model_assembly/formal_assembly_val_test.jsonl"
change_output_format_to_tokens_tags(path_in_sentence, path_in_entities, path_out)

length of f:  399
399 399


[{'tokens': ['#',
   'even',
   'mm',
   'of',
   'now',
   'kit',
   'which',
   'Install',
   'When',
   'against',
   '0',
   '\n'],
  'ner_tags': ['ID',
   'O',
   'DIM',
   'O',
   'O',
   'O',
   'O',
   'OPER',
   'O',
   'RPOS',
   'O',
   'O',
   'O']},
 {'tokens': ['&',
   'into',
   'exhaust',
   'rear',
   '769938',
   'on',
   'case',
   'Housing',
   'Torque',
   'show',
   '-RRB-',
   'for',
   'that',
   'only',
   '-RRB-',
   'accidentally',
   'Torque',
   'through',
   'Hardened',
   'Output',
   'With',
   'Housing',
   'the',
   'into',
   'AeroVee',
   'in',
   ',',
   'screw',
   'optional',
   'second',
   'try',
   "''",
   'of',
   'not',
   'AN3-3A',
   'Output',
   'connector',
   'and',
   'to',
   'Housing',
   '0',
   '\n'],
  'ner_tags': ['O',
   'O',
   'PART',
   'RPOS',
   'ID',
   'O',
   'PART',
   'PART',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'PART',
   'PROP',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   

# fabner, we do not need to run for fabner, ['token', 'ner_tags'] already available

In [46]:
path_in_sentence = "./data/fabNER/fabner_simple_train_original_sentence.jsonl"
path_in_entities = "./data/fabNER/fabner_simple_train_entities.jsonl"
path_out = "./salmon/data_finetuning/finetune_bert_based_entity_model_fabner/formal_fabner_train.jsonl"
process_to_llama2_finetuning_format_for_jsonl(path_in_sentence, path_in_entities, path_out)

9547 9547


In [48]:
path_in_sentence = "./data/fabNER/fabner_simple_val_original_sentence.jsonl"
path_in_entities = "./data/fabNER/fabner_simple_val_entities.jsonl"
path_out = "./salmon/data_finetuning/finetune_bert_based_entity_model_fabner/formal_fabner_val.jsonl"
process_to_llama2_finetuning_format_for_jsonl(path_in_sentence, path_in_entities, path_out)

2200 2200


In [49]:
path_in_sentence = "./data/fabNER/fabner_simple_test_original_sentence.jsonl"
path_in_entities = "./data/fabNER/fabner_simple_test_entities.jsonl"
path_out = "./salmon/data_finetuning/finetune_bert_based_entity_model_fabner/formal_fabner_test.jsonl"
process_to_llama2_finetuning_format_for_jsonl(path_in_sentence, path_in_entities, path_out)

2071 2071


In [2]:
# train_file = "./data/thin-film-processed/1dataset_thin_film_technology_small_sentence.jsonl"
# val_file = "./data/thin-film-processed/1dataset_thin_film_technology_small_sentence.jsonl"
# test_file = "./data/thin-film-processed/1dataset_thin_film_technology_small_sentence.jsonl"
# raw_datasets = load_dataset(
#         "json",
#         data_files={
#             "train": train_file,
#             "validation": val_file,
#             "test": test_file,
#         },
#     )
# raw_datasets

# Start fine-tuning

In [3]:
# The model that you want to train from the Hugging Face hub
#model_name = "NousResearch/Llama-2-7b-chat-hf"
model_name = "NousResearch/Llama-2-7b-hf"
# The instruction dataset to use
#dataset_name = "mlabonne/guanaco-llama2-1k"  # have a "text" column, for question answering tasks
dataset_name = "yahma/alpaca-cleaned"

# Fine-tuned model name
new_model = "llama-2-7b-alpaca-cleaned-small"

################################################################################
# QLoRA parameters
################################################################################

# LoRA attention dimension
lora_r = 64

# Alpha parameter for LoRA scaling
lora_alpha = 16

# Dropout probability for LoRA layers
lora_dropout = 0.1        # 1.0 means no dropout

################################################################################
# bitsandbytes parameters
################################################################################

# Activate 4-bit precision base model loading
use_4bit = True

# Compute dtype for 4-bit base models
bnb_4bit_compute_dtype = "float16"

# Quantization type (fp4 or nf4)
bnb_4bit_quant_type = "nf4"

# Activate nested quantization for 4-bit base models (double quantization)
use_nested_quant = False

################################################################################
# TrainingArguments parameters
################################################################################

# Output directory where the model predictions and checkpoints will be stored
output_dir = "./results"

# Number of training epochs
num_train_epochs = 1

# Enable fp16/bf16 training (set bf16 to True with an A100)
fp16 = False
bf16 = False

# Batch size per GPU for training
per_device_train_batch_size = 4

# Batch size per GPU for evaluation
per_device_eval_batch_size = 4

# Number of update steps to accumulate the gradients for
gradient_accumulation_steps = 1

# Enable gradient checkpointing
gradient_checkpointing = True

# Maximum gradient normal (gradient clipping)
max_grad_norm = 0.3

# Initial learning rate (AdamW optimizer)
learning_rate = 2e-4

# Weight decay to apply to all layers except bias/LayerNorm weights
weight_decay = 0.001

# Optimizer to use
optim = "paged_adamw_32bit"

# Learning rate schedule
lr_scheduler_type = "cosine"

# Number of training steps (overrides num_train_epochs)
max_steps = -1

# Ratio of steps for a linear warmup (from 0 to learning rate)
warmup_ratio = 0.03

# Group sequences into batches with same length
# Saves memory and speeds up training considerably
group_by_length = True

# Save checkpoint every X updates steps
save_steps = 0

# Log every X updates steps
logging_steps = 25

################################################################################
# SFT parameters
################################################################################

# Maximum sequence length to use
max_seq_length = None

# Pack multiple short examples in the same input sequence to increase efficiency
packing = False

# Load the entire model on the GPU 0
device_map = {"": 0}

In [ ]:
# Load dataset (you can process it here)
#dataset = load_dataset(dataset_name, split="train")
#dataset = dataset.train_test_split( test_size=0.999 )["train"]

# Load tokenizer and model with QLoRA configuration
compute_dtype = getattr(torch, bnb_4bit_compute_dtype)

bnb_config = BitsAndBytesConfig(
    load_in_4bit=use_4bit,
    bnb_4bit_quant_type=bnb_4bit_quant_type,
    bnb_4bit_compute_dtype=compute_dtype,
    bnb_4bit_use_double_quant=use_nested_quant,
)

# Check GPU compatibility with bfloat16
if compute_dtype == torch.float16 and use_4bit:
    major, _ = torch.cuda.get_device_capability()
    if major >= 8:
        print("=" * 80)
        print("Your GPU supports bfloat16: accelerate training with bf16=True")
        print("=" * 80)

# Load base model
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    quantization_config=bnb_config,
    device_map=device_map
)
model.config.use_cache = False
model.config.pretraining_tp = 1

# Load LLaMA tokenizer
tokenizer = AutoTokenizer.from_pretrained(model_name, trust_remote_code=True)
tokenizer.pad_token = tokenizer.eos_token
tokenizer.padding_side = "right" # Fix weird overflow issue with fp16 training

DatasetDict({
    train: Dataset({
        features: ['tokens', 'ner_tags'],
        num_rows: 24
    })
    validation: Dataset({
        features: ['tokens', 'ner_tags'],
        num_rows: 24
    })
    test: Dataset({
        features: ['tokens', 'ner_tags'],
        num_rows: 24
    })
})

In [ ]:
dataset_name = "yahma/alpaca-cleaned"
dataset = load_dataset(dataset_name, split="train")
raw_datasets_train = dataset.train_test_split( train_size=0.999999 )["train"]
combined_columns = []
print(len(raw_datasets_train["instruction"]))
for i in range(len(raw_datasets_train["instruction"])):
  row = raw_datasets_train["instruction"][i] + raw_datasets_train["input"][i] + raw_datasets_train["output"][i]
  combined_columns.append(row)

dataset = raw_datasets_train.add_column("text", combined_columns)
#raw_datasets_train.to_csv("train_csv", index=False)
#print(raw_datasets_train)
#dataset = raw_datasets_train

dataset

In [7]:
# Load LoRA configuration
peft_config = LoraConfig(
    lora_alpha=lora_alpha,
    lora_dropout=lora_dropout,
    r=lora_r,
    bias="none",
    task_type="CAUSAL_LM",
)

# Set training parameters
training_arguments = TrainingArguments(
    output_dir=output_dir,
    num_train_epochs=num_train_epochs,
    per_device_train_batch_size=per_device_train_batch_size,
    gradient_accumulation_steps=gradient_accumulation_steps,
    optim=optim,
    save_steps=save_steps,
    logging_steps=logging_steps,
    learning_rate=learning_rate,
    weight_decay=weight_decay,
    fp16=fp16,
    bf16=bf16,
    max_grad_norm=max_grad_norm,
    max_steps=max_steps,
    warmup_ratio=warmup_ratio,
    group_by_length=group_by_length,
    lr_scheduler_type=lr_scheduler_type,
    report_to="tensorboard"
)

def formatting_prompts_func(example):
    text = f"### Instruction: {example['instruction']}\n ### Input: {example['input']}\n ### Output: {example['output']}"
    return text

# trainer = SFTTrainer(
#     model,
#     train_dataset=dataset,
#     formatting_func=formatting_prompts_func,
# )
# trainer.train()

# Set supervised fine-tuning parameters
trainer = SFTTrainer(
    model=model,
    train_dataset=dataset,
    peft_config=peft_config,
    dataset_text_field="text",
    #formatting_func=formatting_prompts_func,
    max_seq_length=max_seq_length,
    tokenizer=tokenizer,
    args=training_arguments,
    packing=packing,
)

# Train model
trainer.train()

# Save trained model
trainer.model.save_pretrained(new_model)

Dataset({
    features: ['output', 'input', 'instruction', 'text'],
    num_rows: 258
})

In [10]:
%load_ext tensorboard
%tensorboard --logdir results/runs

ModuleNotFoundError: No module named 'peft'

### Short test of results

In [ ]:
lora_config = LoraConfig.from_pretrained(new_model)
model = get_peft_model(new_model, lora_config)

In [ ]:
# Ignore warnings
logging.set_verbosity(logging.CRITICAL)

# Run text generation pipeline with our next model
prompt = """
You are an excellent linguist. The task is to extract the entities in the given sentence. The optional entities include PhysicsFlow, InfoFlow, EnergyFlow, Measure, Value, Location, State, Effect, Function, Shape, Component, Attribution, Consequence, System, Material, ScientificConcept, O (others).
Below are some examples.

Example: A narrow track width magnetic head can be formed using an integrated circuit formation techniques such as evaporation plating, chemical etching, etc.
Response of the above example:
narrow track width magnetic head: Component
integrated circuit formation: Function
evaporation plating: Function
chemical etching: Function

Example: But, there has been such a problem that it is difficult to provide a center tap in a conventional thin film magnetic head structure including coils of four or more turns.
Response of the above example:
center tap: Component
conventional: System
thin film magnetic head: Component
structure: System
coils: Component
turns: Component

Example: A magnetic head according to the present invention comprising a coil divided into two sections by the center tap, the electrostatic capacitance of each section being substantially the same.
Response of the above example:
magnetic head: Component
coil: Component
sections: Location
center tap: Component
electrostatic capacitance: EnergyFlow
section: Location


Below is the input sentence, from which you should extract the entities.
Input sentence: A low reemission coefficient is about 0.25 and a high coefficient is about 0.7.
Response of the input sentence:
"""

#prompt = "What is a large language model?"

pipe = pipeline(task="text-generation", model=model, tokenizer=tokenizer, max_length=400)
result = pipe(f"<s>[INST] {prompt} [/INST]")
print(result[0]['generated_text'])